In [0]:
%run "../includes/common_code"

### Ingestion qualifying/qualifying_split*.json
1. Read qualifying/qualifying_split*.json file from raw container using Dataframe reader API
2. Select only the required columns or drop the unwanted columns
3. Rename few columns to the suitable name
4. Add audit column which specifies the ingestion date/time/timestamp

In [0]:
# listing all the mounts
display(dbutils.fs.mounts())

mountPoint source encryptionType /databricks-datasets databricks-datasets /mnt/formula1dl-demo abfss://demo@formula1dlsiddhi.dfs.core.windows.net/ /mnt/formula1dlsiddhi/processed abfss://processed@formula1dlsiddhi.dfs.core.windows.net/ /Volumes UnityCatalogVolumes /mnt/formula1dlsiddhi/demo abfss://demo@formula1dlsiddhi.dfs.core.windows.net/ /databricks/mlflow-tracking databricks/mlflow-tracking /databricks-results databricks-results /mnt/formula1dlsiddhi/raw abfss://raw@formula1dlsiddhi.dfs.core.windows.net/ /databricks/mlflow-registry databricks/mlflow-registry /Volume DbfsReserved /mnt/formula1dlsiddhi/presentation abfss://presentation@formula1dlsiddhi.dfs.core.windows.net/ /volumes DbfsReserved / DatabricksRoot /volume DbfsReserved

In [0]:
# listing all the files in raw container
display(dbutils.fs.ls(raw_container_path))

path name size modificationTime dbfs:/mnt/formula1dlsiddhi/raw/circuits.csv circuits.csv 10044 1743845809000 dbfs:/mnt/formula1dlsiddhi/raw/constructors/ constructors/ 0 1743863074000 dbfs:/mnt/formula1dlsiddhi/raw/constructors.json constructors.json 30415 1743845809000 dbfs:/mnt/formula1dlsiddhi/raw/drivers.json drivers.json 180812 1743845809000 dbfs:/mnt/formula1dlsiddhi/raw/lap_times/ lap_times/ 0 1743845837000 dbfs:/mnt/formula1dlsiddhi/raw/pit_stops.json pit_stops.json 1369387 1743845809000 dbfs:/mnt/formula1dlsiddhi/raw/qualifying/ qualifying/ 0 1743845857000 dbfs:/mnt/formula1dlsiddhi/raw/races.csv races.csv 116847 1743845809000 dbfs:/mnt/formula1dlsiddhi/raw/results.json results.json 7165641 1743845810000

Visit [spark_documentation](https://spark.apache.org/docs/latest/api/python/reference/pyspark.sql/api/pyspark.sql.DataFrameReader.json.html) for read_json()

In [0]:
from pyspark.sql.types import StructType, StructField, StringType, DoubleType, TimestampType, IntegerType, FloatType

#### Defining the schema manually
1. Visit [spark documentation](https://spark.apache.org/docs/latest/api/python/reference/pyspark.sql/api/pyspark.sql.types.StructType.html) for Struct_Type

In [0]:
qualifying_schema = StructType([ StructField("qualifyingId", IntegerType(), False),
                                StructField("raceId", IntegerType(), True),
                                StructField("driverId", IntegerType(), True),
                                StructField("constructorId", IntegerType(), True),
                                StructField("number", IntegerType(), True),
                                StructField("position", IntegerType(), True),
                                StructField("q1", StringType(), True),
                                StructField("q2", StringType(), True),
                                StructField("q3", StringType(), True)
                            ])

In [0]:
qualifying_df = spark.read.schema(qualifying_schema) \
                        .option("header", "true") \
                        .option("multiLine", "true") \
                        .json(f"{raw_container_path}/qualifying/qualifying_split*.json")

In [0]:
# pit_stops schema
qualifying_df.printSchema()

root
 |-- qualifyingId: integer (nullable = true)
 |-- raceId: integer (nullable = true)
 |-- driverId: integer (nullable = true)
 |-- constructorId: integer (nullable = true)
 |-- number: integer (nullable = true)
 |-- position: integer (nullable = true)
 |-- q1: string (nullable = true)
 |-- q2: string (nullable = true)
 |-- q3: string (nullable = true)



In [0]:
display(qualifying_df)

qualifyingId raceId driverId constructorId number position q1 q2 q3 null 18 1 1 22 1 1:26.572 1:25.187 1:26.714 null 18 9 2 4 2 1:26.103 1:25.315 1:26.869 null 18 5 1 23 3 1:25.664 1:25.452 1:27.079 null 18 13 6 2 4 1:25.994 1:25.691 1:27.178 null 18 2 2 3 5 1:25.960 1:25.518 1:27.236 null 18 15 7 11 6 1:26.427 1:26.101 1:28.527 null 18 3 3 7 7 1:26.295 1:26.059 1:28.687 null 18 14 9 9 8 1:26.381 1:26.063 1:29.041 null 18 10 7 12 9 1:26.919 1:26.164 1:29.593 null 18 20 5 15 10 1:26.702 1:25.842 \N null 18 22 11 17 11 1:26.369 1:26.173 \N null 18 4 4 5 12 1:26.907 1:26.188 \N null 18 18 11 16 13 1:26.712 1:26.259 \N null 18 6 3 8 14 1:26.891 1:26.413 \N null 18 17 9 10 15 1:26.914 \N \N null 18 8 6 1 16 1:26.140 \N \N null 18 21 10 21 17 1:27.207 \N \N null 18 7 5 14 18 1:27.446 \N \N null 18 16 10 20 19 1:27.859 \N \N null 18 11 8 18 20 1:28.208 \N \N null 18 12 4 6 21 1:28.330 \N \N null 18 19 8 19 22 1:29.059 \N \N null 19 13 6 2 1 1:35.347 1:34.412 1:35.748 null 19 8 6 1 2 1:35.645 1:34.188 1:36.230 null 19 5 1 23 3 1:35.227 1:34.759 1:36.613 null 19 1 1 22 4 1:35.392 1:34.627 1:36.709 null 19 15 7 11 5 1:35.205 1:34.960 1:36.711 null 19 9 2 4 6 1:35.794 1:34.811 1:36.727 null 19 2 2 3 7 1:35.729 1:34.648 1:36.753 null 19 17 9 10 8 1:35.440 1:34.967 1:37.009 null 19 4 4 5 9 1:35.983 1:35.140 1:38.450 null 19 10 7 12 10 1:35.891 1:35.000 1:39.656 null 19 18 11 16 11 1:35.847 1:35.208 \N null 19 14 9 9 12 1:36.058 1:35.408 \N null 19 12 4 6 13 1:36.074 1:35.562 \N null 19 22 11 17 14 1:36.198 1:35.622 \N null 19 20 5 15 15 1:36.111 1:35.648 \N null 19 3 3 7 16 1:35.843 1:35.670 \N null 19 21 10 21 17 1:36.240 \N \N null 19 6 3 8 18 1:36.388 \N \N null 19 7 5 14 19 1:36.677 \N \N null 19 11 8 18 20 1:37.087 \N \N null 19 16 10 20 21 1:37.101 \N \N null 19 19 8 19 22 1:37.481 \N \N null 20 9 2 4 1 1:32.893 1:31.745 1:33.096 null 20 13 6 2 2 1:31.937 1:31.188 1:33.123 null 20 1 1 22 3 1:32.750 1:31.922 1:33.292 null 20 8 6 1 4 1:32.652 1:31.933 1:33.418 null 20 5 1 23 5 1:33.057 1:31.718 1:33.488 null 20 2 2 3 6 1:33.137 1:31.909 1:33.737 null 20 15 7 11 7 1:32.493 1:32.159 1:33.994 null 20 3 3 7 8 1:32.903 1:32.185 1:34.015 null 20 18 11 16 9 1:32.793 1:32.362 1:35.057 null 20 4 4 5 10 1:32.947 1:32.345 1:35.115 null 20 17 9 10 11 1:33.194 1:32.371 \N null 20 22 11 17 12 1:32.944 1:32.508 \N null 20 10 7 12 13 1:32.800 1:32.528 \N null 20 12 4 6 14 1:32.975 1:32.790 \N null 20 7 5 14 15 1:33.415 1:32.915 \N null 20 6 3 8 16 1:33.386 1:32.943 \N null 20 14 9 9 17 1:33.433 \N \N null 20 21 10 21 18 1:33.501 \N \N null 20 20 5 15 19 1:33.562 \N \N null 20 16 10 20 20 1:33.845 \N \N null 20 19 8 19 21 1:34.140 \N \N null 20 11 8 18 22 1:35.725 \N \N null 21 8 6 1 1 1:20.701 1:20.784 1:21.813 null 21 4 4 5 2 1:21.347 1:20.804 1:21.904 null 21 13 6 2 3 1:21.528 1:20.584 1:22.058 null 21 9 2 4 4 1:21.423 1:20.597 1:22.065 null 21 1 1 22 5 1:21.366 1:20.825 1:22.096 null 21 5 1 23 6 1:21.430 1:20.817 1:22.231 null 21 17 9 10 7 1:21.494 1:20.984 1:22.429 null 21 15 7 11 8 1:21.158 1:20.907 1:22.529 null 21 2 2 3 9 1:21.466 1:20.815 1:22.542 null 21 12 4 6 10 1:21.409 1:20.894 1:22.699 null 21 22 11 17 11 1:21.548 1:21.049 \N null 21 6 3 8 12 1:21.690 1:21.117 \N null 21 18 11 16 13 1:21.757 1:21.211 \N null 21 10 7 12 14 1:21.427 1:21.230 \N null 21 3 3 7 15 1:21.472 1:21.349 \N null 21 7 5 14 16 1:21.540 1:21.724 \N null 21 14 9 9 17 1:21.810 \N \N null 21 20 5 15 18 1:22.108 \N \N null 21 21 10 21 19 1:22.516 \N \N null 21 16 10 20 20 1:23.224 \N \N null 21 19 8 19 21 1:23.318 \N \N null 21 11 8 18 22 1:23.496 \N \N null 22 13 6 2 1 1:25.994 1:26.192 1:27.617 null 22 5 1 23 2 1:26.736 1:26.290 1:27.808 null 22 1 1 22 3 1:26.192 1:26.477 1:27.923 null 22 8 6 1 4 1:26.457 1:26.050 1:27.936 null 22 9 2 4 5 1:26.761 1:26.129 1:28.390 null 22 17 9 10 6 1:26.773 1:26.466 1:28.417 null 22 4 4 5 7 1:26.836 1:26.522 1:28.422 null 22 15 7 11 8 1:26.695 1:26.822 1:28.836 null 22 2 2 3 9 1:27.107 1:27.607 1:28.882 null 22 14 9 9 10 1:26.939 1:26.

#### Further processing 1
1. Rename the following columns
  - qualifyingId ---> qualifying_id
  - driverId ---> driver_id
  - raceId ---> race_id
  - constructorId ---> constructor_id
3. Add the audit column ingestion_date

In [0]:
from pyspark.sql.functions import col, concat, lit, current_timestamp

In [0]:
qualifying_df_final = qualifying_df.withColumnRenamed("raceId", "race_id") \
                                   .withColumnRenamed("driverId", "driver_id") \
                                   .withColumnRenamed("constructorId", "constructor_id") \
                                   .withColumnRenamed("qualifyingId", "qualifying_id")


In [0]:
qualifying_df_final = ingest_current_timestamp(qualifying_df_final)

In [0]:
display(qualifying_df_final)

qualifying_id race_id driver_id constructor_id number position q1 q2 q3 ingest_date null 18 1 1 22 1 1:26.572 1:25.187 1:26.714 2025-04-06T11:31:05.917Z null 18 9 2 4 2 1:26.103 1:25.315 1:26.869 2025-04-06T11:31:05.917Z null 18 5 1 23 3 1:25.664 1:25.452 1:27.079 2025-04-06T11:31:05.917Z null 18 13 6 2 4 1:25.994 1:25.691 1:27.178 2025-04-06T11:31:05.917Z null 18 2 2 3 5 1:25.960 1:25.518 1:27.236 2025-04-06T11:31:05.917Z null 18 15 7 11 6 1:26.427 1:26.101 1:28.527 2025-04-06T11:31:05.917Z null 18 3 3 7 7 1:26.295 1:26.059 1:28.687 2025-04-06T11:31:05.917Z null 18 14 9 9 8 1:26.381 1:26.063 1:29.041 2025-04-06T11:31:05.917Z null 18 10 7 12 9 1:26.919 1:26.164 1:29.593 2025-04-06T11:31:05.917Z null 18 20 5 15 10 1:26.702 1:25.842 \N 2025-04-06T11:31:05.917Z null 18 22 11 17 11 1:26.369 1:26.173 \N 2025-04-06T11:31:05.917Z null 18 4 4 5 12 1:26.907 1:26.188 \N 2025-04-06T11:31:05.917Z null 18 18 11 16 13 1:26.712 1:26.259 \N 2025-04-06T11:31:05.917Z null 18 6 3 8 14 1:26.891 1:26.413 \N 2025-04-06T11:31:05.917Z null 18 17 9 10 15 1:26.914 \N \N 2025-04-06T11:31:05.917Z null 18 8 6 1 16 1:26.140 \N \N 2025-04-06T11:31:05.917Z null 18 21 10 21 17 1:27.207 \N \N 2025-04-06T11:31:05.917Z null 18 7 5 14 18 1:27.446 \N \N 2025-04-06T11:31:05.917Z null 18 16 10 20 19 1:27.859 \N \N 2025-04-06T11:31:05.917Z null 18 11 8 18 20 1:28.208 \N \N 2025-04-06T11:31:05.917Z null 18 12 4 6 21 1:28.330 \N \N 2025-04-06T11:31:05.917Z null 18 19 8 19 22 1:29.059 \N \N 2025-04-06T11:31:05.917Z null 19 13 6 2 1 1:35.347 1:34.412 1:35.748 2025-04-06T11:31:05.917Z null 19 8 6 1 2 1:35.645 1:34.188 1:36.230 2025-04-06T11:31:05.917Z null 19 5 1 23 3 1:35.227 1:34.759 1:36.613 2025-04-06T11:31:05.917Z null 19 1 1 22 4 1:35.392 1:34.627 1:36.709 2025-04-06T11:31:05.917Z null 19 15 7 11 5 1:35.205 1:34.960 1:36.711 2025-04-06T11:31:05.917Z null 19 9 2 4 6 1:35.794 1:34.811 1:36.727 2025-04-06T11:31:05.917Z null 19 2 2 3 7 1:35.729 1:34.648 1:36.753 2025-04-06T11:31:05.917Z null 19 17 9 10 8 1:35.440 1:34.967 1:37.009 2025-04-06T11:31:05.917Z null 19 4 4 5 9 1:35.983 1:35.140 1:38.450 2025-04-06T11:31:05.917Z null 19 10 7 12 10 1:35.891 1:35.000 1:39.656 2025-04-06T11:31:05.917Z null 19 18 11 16 11 1:35.847 1:35.208 \N 2025-04-06T11:31:05.917Z null 19 14 9 9 12 1:36.058 1:35.408 \N 2025-04-06T11:31:05.917Z null 19 12 4 6 13 1:36.074 1:35.562 \N 2025-04-06T11:31:05.917Z null 19 22 11 17 14 1:36.198 1:35.622 \N 2025-04-06T11:31:05.917Z null 19 20 5 15 15 1:36.111 1:35.648 \N 2025-04-06T11:31:05.917Z null 19 3 3 7 16 1:35.843 1:35.670 \N 2025-04-06T11:31:05.917Z null 19 21 10 21 17 1:36.240 \N \N 2025-04-06T11:31:05.917Z null 19 6 3 8 18 1:36.388 \N \N 2025-04-06T11:31:05.917Z null 19 7 5 14 19 1:36.677 \N \N 2025-04-06T11:31:05.917Z null 19 11 8 18 20 1:37.087 \N \N 2025-04-06T11:31:05.917Z null 19 16 10 20 21 1:37.101 \N \N 2025-04-06T11:31:05.917Z null 19 19 8 19 22 1:37.481 \N \N 2025-04-06T11:31:05.917Z null 20 9 2 4 1 1:32.893 1:31.745 1:33.096 2025-04-06T11:31:05.917Z null 20 13 6 2 2 1:31.937 1:31.188 1:33.123 2025-04-06T11:31:05.917Z null 20 1 1 22 3 1:32.750 1:31.922 1:33.292 2025-04-06T11:31:05.917Z null 20 8 6 1 4 1:32.652 1:31.933 1:33.418 2025-04-06T11:31:05.917Z null 20 5 1 23 5 1:33.057 1:31.718 1:33.488 2025-04-06T11:31:05.917Z null 20 2 2 3 6 1:33.137 1:31.909 1:33.737 2025-04-06T11:31:05.917Z null 20 15 7 11 7 1:32.493 1:32.159 1:33.994 2025-04-06T11:31:05.917Z null 20 3 3 7 8 1:32.903 1:32.185 1:34.015 2025-04-06T11:31:05.917Z null 20 18 11 16 9 1:32.793 1:32.362 1:35.057 2025-04-06T11:31:05.917Z null 20 4 4 5 10 1:32.947 1:32.345 1:35.115 2025-04-06T11:31:05.917Z null 20 17 9 10 11 1:33.194 1:32.371 \N 2025-04-06T11:31:05.917Z null 20 22 11 17 12 1:32.944 1:32.508 \N 2025-04-06T11:31:05.917Z null 20 10 7 12 13 1:32.800 1:32.528 \N 2025-04-06T11:31:05.917Z null 20 12 4 6 14 1:32.975 1:32.790 \N 2025-04-06T11:31:05.917Z null 20 7 5 14 15 1:33.415 1:32.915 \N 2025-04-06T11:31:05.917Z null 20 6 3 8 16 1:33.386 1:32.943 \N 2025-04-06T11:31:05.9

#### Write the final data into processed folder
1. Visit [spark documentation](https://spark.apache.org/docs/latest/api/python/reference/pyspark.sql/api/pyspark.sql.DataFrame.write.html?highlight=write) for write()

In [0]:
qualifying_df_final.write.mode("overwrite") \
                      .parquet(f"{processed_container_path}/qualifying")

In [0]:
# Verify that the data was written to the parquet file
df = spark.read.parquet(f"{processed_container_path}/qualifying")
display(df)

qualifying_id race_id driver_id constructor_id number position q1 q2 q3 ingest_date null 18 1 1 22 1 1:26.572 1:25.187 1:26.714 2025-04-06T11:31:22.596Z null 18 9 2 4 2 1:26.103 1:25.315 1:26.869 2025-04-06T11:31:22.596Z null 18 5 1 23 3 1:25.664 1:25.452 1:27.079 2025-04-06T11:31:22.596Z null 18 13 6 2 4 1:25.994 1:25.691 1:27.178 2025-04-06T11:31:22.596Z null 18 2 2 3 5 1:25.960 1:25.518 1:27.236 2025-04-06T11:31:22.596Z null 18 15 7 11 6 1:26.427 1:26.101 1:28.527 2025-04-06T11:31:22.596Z null 18 3 3 7 7 1:26.295 1:26.059 1:28.687 2025-04-06T11:31:22.596Z null 18 14 9 9 8 1:26.381 1:26.063 1:29.041 2025-04-06T11:31:22.596Z null 18 10 7 12 9 1:26.919 1:26.164 1:29.593 2025-04-06T11:31:22.596Z null 18 20 5 15 10 1:26.702 1:25.842 \N 2025-04-06T11:31:22.596Z null 18 22 11 17 11 1:26.369 1:26.173 \N 2025-04-06T11:31:22.596Z null 18 4 4 5 12 1:26.907 1:26.188 \N 2025-04-06T11:31:22.596Z null 18 18 11 16 13 1:26.712 1:26.259 \N 2025-04-06T11:31:22.596Z null 18 6 3 8 14 1:26.891 1:26.413 \N 2025-04-06T11:31:22.596Z null 18 17 9 10 15 1:26.914 \N \N 2025-04-06T11:31:22.596Z null 18 8 6 1 16 1:26.140 \N \N 2025-04-06T11:31:22.596Z null 18 21 10 21 17 1:27.207 \N \N 2025-04-06T11:31:22.596Z null 18 7 5 14 18 1:27.446 \N \N 2025-04-06T11:31:22.596Z null 18 16 10 20 19 1:27.859 \N \N 2025-04-06T11:31:22.596Z null 18 11 8 18 20 1:28.208 \N \N 2025-04-06T11:31:22.596Z null 18 12 4 6 21 1:28.330 \N \N 2025-04-06T11:31:22.596Z null 18 19 8 19 22 1:29.059 \N \N 2025-04-06T11:31:22.596Z null 19 13 6 2 1 1:35.347 1:34.412 1:35.748 2025-04-06T11:31:22.596Z null 19 8 6 1 2 1:35.645 1:34.188 1:36.230 2025-04-06T11:31:22.596Z null 19 5 1 23 3 1:35.227 1:34.759 1:36.613 2025-04-06T11:31:22.596Z null 19 1 1 22 4 1:35.392 1:34.627 1:36.709 2025-04-06T11:31:22.596Z null 19 15 7 11 5 1:35.205 1:34.960 1:36.711 2025-04-06T11:31:22.596Z null 19 9 2 4 6 1:35.794 1:34.811 1:36.727 2025-04-06T11:31:22.596Z null 19 2 2 3 7 1:35.729 1:34.648 1:36.753 2025-04-06T11:31:22.596Z null 19 17 9 10 8 1:35.440 1:34.967 1:37.009 2025-04-06T11:31:22.596Z null 19 4 4 5 9 1:35.983 1:35.140 1:38.450 2025-04-06T11:31:22.596Z null 19 10 7 12 10 1:35.891 1:35.000 1:39.656 2025-04-06T11:31:22.596Z null 19 18 11 16 11 1:35.847 1:35.208 \N 2025-04-06T11:31:22.596Z null 19 14 9 9 12 1:36.058 1:35.408 \N 2025-04-06T11:31:22.596Z null 19 12 4 6 13 1:36.074 1:35.562 \N 2025-04-06T11:31:22.596Z null 19 22 11 17 14 1:36.198 1:35.622 \N 2025-04-06T11:31:22.596Z null 19 20 5 15 15 1:36.111 1:35.648 \N 2025-04-06T11:31:22.596Z null 19 3 3 7 16 1:35.843 1:35.670 \N 2025-04-06T11:31:22.596Z null 19 21 10 21 17 1:36.240 \N \N 2025-04-06T11:31:22.596Z null 19 6 3 8 18 1:36.388 \N \N 2025-04-06T11:31:22.596Z null 19 7 5 14 19 1:36.677 \N \N 2025-04-06T11:31:22.596Z null 19 11 8 18 20 1:37.087 \N \N 2025-04-06T11:31:22.596Z null 19 16 10 20 21 1:37.101 \N \N 2025-04-06T11:31:22.596Z null 19 19 8 19 22 1:37.481 \N \N 2025-04-06T11:31:22.596Z null 20 9 2 4 1 1:32.893 1:31.745 1:33.096 2025-04-06T11:31:22.596Z null 20 13 6 2 2 1:31.937 1:31.188 1:33.123 2025-04-06T11:31:22.596Z null 20 1 1 22 3 1:32.750 1:31.922 1:33.292 2025-04-06T11:31:22.596Z null 20 8 6 1 4 1:32.652 1:31.933 1:33.418 2025-04-06T11:31:22.596Z null 20 5 1 23 5 1:33.057 1:31.718 1:33.488 2025-04-06T11:31:22.596Z null 20 2 2 3 6 1:33.137 1:31.909 1:33.737 2025-04-06T11:31:22.596Z null 20 15 7 11 7 1:32.493 1:32.159 1:33.994 2025-04-06T11:31:22.596Z null 20 3 3 7 8 1:32.903 1:32.185 1:34.015 2025-04-06T11:31:22.596Z null 20 18 11 16 9 1:32.793 1:32.362 1:35.057 2025-04-06T11:31:22.596Z null 20 4 4 5 10 1:32.947 1:32.345 1:35.115 2025-04-06T11:31:22.596Z null 20 17 9 10 11 1:33.194 1:32.371 \N 2025-04-06T11:31:22.596Z null 20 22 11 17 12 1:32.944 1:32.508 \N 2025-04-06T11:31:22.596Z null 20 10 7 12 13 1:32.800 1:32.528 \N 2025-04-06T11:31:22.596Z null 20 12 4 6 14 1:32.975 1:32.790 \N 2025-04-06T11:31:22.596Z null 20 7 5 14 15 1:33.415 1:32.915 \N 2025-04-06T11:31:22.596Z null 20 6 3 8 16 1:33.386 1:32.943 \N 2025-04-06T11:31:22.5

In [0]:
dbutils.notebook.exit("Success...")